In [3]:
!git clone https://gitlab.com/airatb1508/domclick-parser.git


Cloning into 'domclick-parser'...


In [4]:
%pip install requests

  Using cached requests-2.32.3-py3-none-any.whl.metadata (4.6 kB)
  Using cached charset_normalizer-3.4.0-cp39-cp39-win_amd64.whl.metadata (34 kB)
  Using cached idna-3.10-py3-none-any.whl.metadata (10 kB)
  Using cached urllib3-2.2.3-py3-none-any.whl.metadata (6.5 kB)
  Using cached certifi-2024.8.30-py3-none-any.whl.metadata (2.2 kB)
Using cached requests-2.32.3-py3-none-any.whl (64 kB)
Using cached certifi-2024.8.30-py3-none-any.whl (167 kB)
Using cached charset_normalizer-3.4.0-cp39-cp39-win_amd64.whl (102 kB)
Using cached idna-3.10-py3-none-any.whl (70 kB)
Using cached urllib3-2.2.3-py3-none-any.whl (126 kB)


In [3]:
import json
import requests
import hashlib
import pandas as pd
from datetime import datetime


class DomClickApi:
    def __init__(self):
        self.session = requests.Session()
        self.session.headers.update({"X-Service": "true",
                                     "Connection": "Keep-Alive",
                                     "User-Agent": "Android; 12; Google; google_pixel_5; 8.72.0; 8720006; ; NONAUTH"
                                     })

        # init (get cookies)
        self.get("https://api.domclick.ru/core/no-auth-zone/api/v1/ensure_session")
        self.get("https://ipoteka.domclick.ru/mobile/v1/feature_toggles")

    def get(self, url, **kwargs):
        self.__update_headers(url, **kwargs)
        result = self.session.get(url, **kwargs)
        print(self.session.cookies.get_dict())
        return result

    def __update_headers(self, url, **kwargs):
        url = self.__get_prepared_url(url, **kwargs)
        sault = "ad65f331b02b90d868cbdd660d82aba0"
        timestamp = str(int(datetime.now().timestamp()))
        encoded = (sault + url + timestamp).encode("UTF-8")
        h = hashlib.md5(encoded).hexdigest()
        self.session.headers.update({"Timestamp": timestamp,
                                     "Hash": "v1:" + h,
                                     })

    def __get_prepared_url(self, url, **kwargs):
        p = requests.models.PreparedRequest()
        p.prepare(method="GET", url=url, **kwargs)
        return p.url


def pprint_json(json_str):
    try:
        json_object = json.loads(json_str)
        json_formatted_str = json.dumps(json_object, indent=2, ensure_ascii=False).encode('utf8')
        print(json_formatted_str.decode())
    except:
        print(json_str)


offers_url = 'https://offers-service.domclick.ru/research/v5/offers/'
count_url = 'https://offers-service.domclick.ru/research/v5/offers/count/'

dca = DomClickApi()
res = dca.get(count_url, params={
    "address": "26f533ee-f4c6-4fd8-9cb5-a1910250622e",  # UUID региона
    "deal_type": "sale",  # Тип сделки: Купить
    "category": "living",  # Категория: Жилье
    "offer_type": ["flat", "layout"],  # Тип недвижимости: квартира (вторичка/новостройка)
    "rooms": ["1", "2"],  # Кол-во комнат: 1 и 2
    "area__gte": 50,  # Площадь от 50 кв.м
    "floor__gte": 7,  # Этаж от 7
    "sort": "qi",  # Сортировка по рекомендуемым
    "sort_dir": "desc",  # По убыванию
    "offset": 0,
    "limit": 30  # Лимит выборки
})
print("RES:", res)
print(res.text)
pprint_json(res.text)

count_obj = json.loads(res.text)
total = count_obj["pagination"]["total"]

# Инициализация списка для сохранения данных предложений
offers_list = []
offset = 0

while offset < total:
    res = dca.get(offers_url, params={
        "address": "26f533ee-f4c6-4fd8-9cb5-a1910250622e",
        "deal_type": "sale",
        "category": "living",
        "offer_type": ["flat", "layout"],
        "rooms": ["1", "2"],
        "area__gte": 50,
        "floor__gte": 7,

        "sort": "qi",
        "sort_dir": "desc",
        "offset": offset,
        "limit": 30,
    })
    print("RES:", res)
    pprint_json(res.text)
    
    # Загружаем предложения, если ключ 'items' существует
    offers_obj = json.loads(res.text)
    if 'items' in offers_obj['result']:
        offers_list.extend(offers_obj['result']['items'])  # Сохраняем объекты предложений
        total = offers_obj["pagination"]["total"]
    else:
        print(f"Ключ 'items' отсутствует в ответе: {offers_obj}")
        break  # Останавливаем выполнение, если ключ 'items' не найден

    print(f"{offset}/{total}")
    offset += 30

{'ns_session': 'fa39230c-95a2-4d01-a92b-6411a66775bc', 'qrator_ssid2': 'v2.0.1729753682.638.51056f16NE0IuRSj|kdXIx3PCC9iwmY9R|rw9ahE7oynep2He3J+a5hnczmHZH/7PsWXJEtyYxtM0aN9hxwWaA2/qD3w6OdlmpNGLQ2scVjppOyr11MxdTXw==-zSLi2qz3r0w1tGBmakLcWlj4i2s='}
{'ftgl_cookie_id': 'f46b818011c2d1c4e7316f24f6e7c16a', 'ns_session': 'fa39230c-95a2-4d01-a92b-6411a66775bc', 'qrator_ssid2': 'v2.0.1729753682.638.51056f16NE0IuRSj|kdXIx3PCC9iwmY9R|rw9ahE7oynep2He3J+a5hnczmHZH/7PsWXJEtyYxtM0aN9hxwWaA2/qD3w6OdlmpNGLQ2scVjppOyr11MxdTXw==-zSLi2qz3r0w1tGBmakLcWlj4i2s='}
{'ftgl_cookie_id': 'f46b818011c2d1c4e7316f24f6e7c16a', 'ns_session': 'fa39230c-95a2-4d01-a92b-6411a66775bc', 'qrator_ssid2': 'v2.0.1729753682.638.51056f16NE0IuRSj|kdXIx3PCC9iwmY9R|rw9ahE7oynep2He3J+a5hnczmHZH/7PsWXJEtyYxtM0aN9hxwWaA2/qD3w6OdlmpNGLQ2scVjppOyr11MxdTXw==-zSLi2qz3r0w1tGBmakLcWlj4i2s='}
RES: <Response [200]>
{"success":true,"pagination":{"offset":0,"limit":30,"total":2537},"result":{}}
{
  "success": true,
  "pagination": {
    "offset": 

In [5]:
exel_export = pd.DataFrame(offers_list)
exel_export

renovation  \
0    {'type': 'pre_finish', 'display_name': 'Предчи...   
1                                                  NaN   
2    {'type': 'rough_finish', 'display_name': 'Черн...   
3    {'type': 'no_renovation', 'display_name': 'Без...   
4                                                  NaN   
..                                                 ...   
736                                                NaN   
737                                                NaN   
738                                                NaN   
739                                                NaN   
740                                                NaN   

                              placement_type has_big_check offer_type  \
0    [parking_spaces, storages, commercials]          True     layout   
1                                        NaN           NaN       flat   
2                                         []          True     layout   
3    [storages, commercials, parking_spaces]          True     layout   
4                                        NaN           NaN       flat   
..                                       ...           ...        ...   
736                                      NaN           NaN       flat   
737                                      NaN           NaN       flat   
738                                      NaN           NaN       flat   
739                                      NaN           NaN       flat   
740                                      NaN           NaN       flat   

                                   discount_status  \
0                                               {}   
1    {'status': 'discount_received', 'value': 0.6}   
2                                               {}   
3                                               {}   
4                     {'status': 'discount_error'}   
..                                             ...   
736  {'status': 'discount_received', 'value': 0.6}   
737  {'status': 'discount_received', 'value': 0.3}   
738  {'status': 'discount_received', 'value': 0.6}   
739  {'status': 'discount_received', 'value': 0.6}   
740  {'status': 'discount_received', 'value': 0.6}   

                                             developer  \
0    {'logo': '/s200x200q80/partnerhub/logos/8f/4d/...   
1                                                  NaN   
2    {'logo': '/s200x200q80/partnerhub/logos/fd/52/...   
3    {'logo': '/s200x200q80/partnerhub/logos/03/35/...   
4                                                  NaN   
..                                                 ...   
736                                                NaN   
737                                                NaN   
738                                                NaN   
739                                                NaN   
740                                                NaN   

                                               complex  trade_in  \
0    {'id': 117869, 'name': 'ЖК Сиберово', 'has_mor...     False   
1                                                  NaN     False   
2    {'id': 115770, 'name': 'ЖК Аквамарин', 'has_mo...     False   
3    {'id': 116757, 'name': 'ЖК "Savin Family" (Сав...     False   
4                                                  NaN     False   
..                                                 ...       ...   
736                                                NaN     False   
737                                                NaN     False   
738                                                NaN     False   
739                                                NaN     False   
740                                                NaN     False   

                         published_dt       layout_id  ...  assignment_sale  \
0    2024-10-24T00:24:08.242704+00:00  171022-53dot60  ...              NaN   
1    2024-08-13T10:08:18.212940+00:00             NaN  ...            False   
2    2024-10-24T02:37:19.242008+00:00  182804-61dot36  ...            

In [10]:
exel_export.columns

Index(['renovation', 'placement_type', 'has_big_check', 'offer_type',
       'discount_status', 'developer', 'complex', 'trade_in', 'published_dt',
       'layout_id', 'min_rate', 'status', 'photos', 'chat_available',
       'payment_order_id', 'id', 'object_info', 'backwash', 'source',
       'address', 'offers_count', 'slug', 'is_auction', 'house', 'description',
       'price_info', 'deal_type', 'last_price_history_state', 'ipoteka_rate',
       'monthly_payment', 'legal_options', 'seo_info', 'has_advance_payment',
       'updated_dt', 'seo', 'pessimization', 'duplicates_offer_count',
       'is_placement_paid', 'seller', 'assignment_sale', 'tariff_options',
       'category', 'online_show', 'is_exclusive', 'flat_complex',
       'rooms_offered', 'profit_badge', 'land', 'video'],
      dtype='object')

In [ ]:
# Преобразование списка предложений в DataFrame
if offers_list:
    exel_export = pd.DataFrame(offers_list)

    # Определяем нужные колонки (проверьте, что все ключи существуют в данных предложений)
    columns = [
        'address', 'deal_type', 'category', 'offer_type', 'rooms', 'area', 'floor', 
        'kitchen_area', 'floor_not_first', 'floor_not_last', 'balconies', 'has_connected_bathrooms', 
        'has_separated_bathrooms', 'renovation', 'window_view', 'floors__gte', 'floors__lte', 
        'build_year__gte', 'build_year__lte', 'building_completion_year', 'wall_type', 
        'has_lifts', 'has_freight_lifts', 'is_apartment', 'sell_type', 'is_owner', 
        'from_developer', 'is_sber', 'published_filter'
    ]

    # Выбираем только нужные колонки и экспортируем в CSV
    selected_columns = exel_export[columns]
    selected_columns.to_csv('Domparsing.csv', mode='a', header=False, index=False)
else:
    print("Нет данных для экспорта.")